In [18]:
import altair
from numba import njit, int64, float64
from numba.typed import List
import polars as pl
import numpy as np
from hftbacktest import BacktestAsset, HashMapMarketDepthBacktest, LIMIT, GTC, NONE, NEW, FILLED, CANCELED, EXPIRED, GTX, Recorder

In [19]:
@njit
def print_bbo(hbt):
    # Iterating until hftbacktest reaches the end of data.
    # Elapses 60-sec every iteration.
    # Time unit is the same as data's timestamp's unit.
    # Timestamp of the sample data is in nanoseconds.
    while hbt.elapse(60 * 1e9) == 0:
        # Gets the market depth for the first asset.
        depth = hbt.depth(0)

        # Prints the best bid and the best offer.
        print(
            'current_timestamp:', hbt.current_timestamp,
            ', best_bid:', np.round(depth.best_bid, 5),
            ', best_ask:', np.round(depth.best_ask, 5)
        )
    return True


@njit
def print_3depth(hbt):
    while hbt.elapse(60 * 1e9) == 0:
        print('current_timestamp:', hbt.current_timestamp)

        # Gets the market depth for the first asset, in the same order as when you created the backtest.
        depth = hbt.depth(0)

        # a key of bid_depth or ask_depth is price in ticks.
        # (integer) price_tick = price / tick_size
        i = 0
        for tick_price in range(depth.best_ask_tick, depth.best_ask_tick + 100):
            qty = depth.ask_qty_at_tick(tick_price)
            if qty > 0:
                print(
                    'ask: ',
                    qty,
                    '@',
                    np.round(tick_price * depth.tick_size, 5)
                )

                i += 1
                if i == 3:
                    break
        i = 0
        for tick_price in range(depth.best_bid_tick, max(depth.best_bid_tick - 100, 0), -1):
            qty = depth.bid_qty_at_tick(tick_price)
            if qty > 0:
                print(
                    'bid: ',
                    qty,
                    '@',
                    np.round(tick_price * depth.tick_size, 5)
                )

                i += 1
                if i == 3:
                    break
    return True

In [20]:
asset = (
    BacktestAsset()
    .data(['binance_20240601.npz'])
    .linear_asset(1.0)
    .constant_latency(10_000_000, 10_000_000)
    .log_prob_queue_model()
    .risk_adverse_queue_model()
    .no_partial_fill_exchange()
    .trading_value_fee_model(-0.00005,0.00015)
    .tick_size(.00001)
    .lot_size(0.1)
    .last_trades_capacity(1)
)

In [21]:
hbt = HashMapMarketDepthBacktest([asset])
print_3depth(hbt)
hbt.close()


current_timestamp: 1717200060131000000
ask:  8.054 @ 67608.7
bid:  1.346 @ 67608.6
current_timestamp: 1717200120131000000
ask:  11.524 @ 67597.1
bid:  1.543 @ 67597.0
current_timestamp: 1717200180131000000
ask:  5.661 @ 67619.6
bid:  0.279 @ 67619.5
current_timestamp: 1717200240131000000
ask:  1.574 @ 67641.6
bid:  8.642 @ 67641.5
current_timestamp: 1717200300131000000
ask:  0.907 @ 67680.4
bid:  15.946 @ 67680.3
current_timestamp: 1717200360131000000
ask:  0.39 @ 67675.1
bid:  8.783 @ 67675.0
current_timestamp: 1717200420131000000
ask:  2.723 @ 67675.3
bid:  4.568 @ 67675.2
current_timestamp: 1717200480131000000
ask:  14.337 @ 67697.1
bid:  3.361 @ 67697.0
current_timestamp: 1717200540131000000
ask:  13.375 @ 67678.2
bid:  2.424 @ 67678.1
current_timestamp: 1717200600131000000
ask:  11.086 @ 67641.7
bid:  1.919 @ 67641.6
current_timestamp: 1717200660131000000
ask:  11.676 @ 67655.0
bid:  7.847 @ 67654.9
current_timestamp: 1717200720131000000
ask:  3.511 @ 67644.4
bid:  3.738 @ 67644.3

0

In [22]:
hbt = HashMapMarketDepthBacktest([asset])
print_bbo(hbt)
hbt.close()

current_timestamp: 1717200060131000000 , best_bid: 67608.6 , best_ask: 67608.7
current_timestamp: 1717200120131000000 , best_bid: 67597.0 , best_ask: 67597.1
current_timestamp: 1717200180131000000 , best_bid: 67619.5 , best_ask: 67619.6
current_timestamp: 1717200240131000000 , best_bid: 67641.5 , best_ask: 67641.6
current_timestamp: 1717200300131000000 , best_bid: 67680.3 , best_ask: 67680.4
current_timestamp: 1717200360131000000 , best_bid: 67675.0 , best_ask: 67675.1
current_timestamp: 1717200420131000000 , best_bid: 67675.2 , best_ask: 67675.3
current_timestamp: 1717200480131000000 , best_bid: 67697.0 , best_ask: 67697.1
current_timestamp: 1717200540131000000 , best_bid: 67678.1 , best_ask: 67678.2
current_timestamp: 1717200600131000000 , best_bid: 67641.6 , best_ask: 67641.7
current_timestamp: 1717200660131000000 , best_bid: 67654.9 , best_ask: 67655.0
current_timestamp: 1717200720131000000 , best_bid: 67644.3 , best_ask: 67644.4
current_timestamp: 1717200780131000000 , best_bid: 6

0

In [23]:
@njit
def print_orders(hbt):
    # You can access open orders and also closed orders via hbt.orders.
    # Gets the OrderDict for the first asset.
    orders = hbt.orders(0)

    # hbt.orders is a dictionary, but be aware that it does not support all dict methods, and its keys are order_id (int).
    order_values = orders.values()
    while order_values.has_next():
        order = order_values.get()

        order_status = ''
        if order.status == NONE:
            order_status = 'NONE' # Exchange hasn't received an order yet.
        elif order.status == NEW:
            order_status = 'NEW'
        elif order.status == FILLED:
            order_status = 'FILLED'
        elif order.status == CANCELED:
            order_status = 'CANCELED'
        elif order.status == EXPIRED:
            order_status = 'EXPIRED'

        order_req = ''
        if order.req == NONE:
            order_req = 'NONE'
        elif order.req == NEW:
            order_req = 'NEW'
        elif order.req == CANCELED:
            order_req = 'CANCEL'

        print(
            'current_timestamp:', hbt.current_timestamp,
             ', order_id:', order.order_id,
             ', order_price:', np.round(order.price, 5),
             ', order_qty:', order.qty,
             ', order_status:', order_status,
             ', order_req:', order_req
        )

@njit
def submit_order(hbt):
    is_order_submitted = False
    while hbt.elapse(30 * 1e9) == 0:
        # Prints open orders.
        print_orders(hbt)

        depth = hbt.depth(0)

        if not is_order_submitted:
            # Submits a buy order at 300 ticks below the best bid for the first asset.
            order_id = 1
            order_price = depth.best_bid - 300 * depth.tick_size
            order_qty = 1
            time_in_force = GTC # Good 'till cancel
            order_type = LIMIT
            hbt.submit_buy_order(0, order_id, order_price, order_qty, time_in_force, order_type, False)
            is_order_submitted = True
    return True

In [24]:
hbt = HashMapMarketDepthBacktest([asset])
submit_order(hbt)
hbt.close()

current_timestamp: 1717200060131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200090131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200120131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200150131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200180131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200210131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200240131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE
current_timestamp: 1717200270131000000 , order_i

0

In [25]:
@njit
def clear_inactive_orders(hbt):
    is_order_submitted = False
    while hbt.elapse(30 * 1e9) == 0:
        print_orders(hbt)

        # Removes inactive(FILLED, CANCELED, EXPIRED) orders from hbt.orders for the first asset.
        hbt.clear_inactive_orders(0)

        depth = hbt.depth(0)

        if not is_order_submitted:
            order_id = 1
            order_price = depth.best_bid - 300 * depth.tick_size
            order_qty = 1
            time_in_force = GTC
            order_type = LIMIT
            hbt.submit_buy_order(0, order_id, order_price, order_qty, time_in_force, order_type, False)
            is_order_submitted = True
    return True

In [26]:
hbt = HashMapMarketDepthBacktest([asset])
clear_inactive_orders(hbt)
hbt.close()

current_timestamp: 1717200060131000000 , order_id: 1 , order_price: 67601.697 , order_qty: 1.0 , order_status: FILLED , order_req: NONE


KeyboardInterrupt: 

In [ ]:
@njit
def watch_pending(hbt):
    is_order_submitted = False
    # Elapses 0.01-sec every iteration.
    while hbt.elapse(0.01 * 1e9) == 0:
        print_orders(hbt)

        hbt.clear_inactive_orders(0)

        depth = hbt.depth(0)

        if not is_order_submitted:
            order_id = 1
            order_price = depth.best_bid - 300 * depth.tick_size
            order_qty = 1
            time_in_force = GTC
            order_type = LIMIT
            hbt.submit_buy_order(0, order_id, order_price, order_qty, time_in_force, order_type, False)
            is_order_submitted = True

        # Prevents too many prints
        orders = hbt.orders(0)
        order = orders.get(order_id)
        if order.status == NEW:
            return False
    return True

In [ ]:
hbt = HashMapMarketDepthBacktest([asset])
watch_pending(hbt)
hbt.close()

In [ ]:
@njit
def wait_for_order_response(hbt):
    order_id = 0
    is_order_submitted = False
    while hbt.elapse(0.01 * 1e9) == 0:
        print_orders(hbt)

        hbt.clear_inactive_orders(0)

        # Prevents too many prints
        orders = hbt.orders(0)
        if order_id in orders:
            if orders.get(order_id).status == NEW:
                return False

        depth = hbt.depth(0)

        if not is_order_submitted:
            order_id = 1
            order_price = depth.best_bid
            order_qty = 1
            time_in_force = GTC
            order_type = LIMIT
            hbt.submit_buy_order(0, order_id, order_price, order_qty, time_in_force, order_type, False)
            # Waits for the order response for a given order id for the first asset.
            print('an order is submitted at', hbt.current_timestamp)

            # Timeout is set 1-second.
            hbt.wait_order_response(0, order_id, 1 * 1e9)
            print('an order response is received at', hbt.current_timestamp)
            is_order_submitted = True
    return True

In [ ]:
hbt = HashMapMarketDepthBacktest([asset])
wait_for_order_response(hbt)
hbt.close()

In [ ]:
@njit
def position(hbt):
    is_order_submitted = False
    while hbt.elapse(60 * 1e9) == 0:
        print_orders(hbt)

        hbt.clear_inactive_orders(0)

        # Prints position
        print(
            'current_timestamp:', hbt.current_timestamp,
            ', position:', hbt.position(0),
            ', balance:', hbt.state_values(0).balance,
            ', fee:', hbt.state_values(0).fee
        )

        depth = hbt.depth(0)

        if not is_order_submitted:
            order_id = 1
            order_price = depth.best_bid
            order_qty = 1
            time_in_force = GTC
            order_type = LIMIT
            hbt.submit_buy_order(0, order_id, order_price, order_qty, time_in_force, order_type, False)

            # Timeout is set 1-second.
            hbt.wait_order_response(0, order_id, 1e9)
            is_order_submitted = True
    return True
hbt = HashMapMarketDepthBacktest([asset])
position(hbt)
_ = hbt.close()

In [27]:
@njit
def plot_bbo(hbt, local_timestamp, best_bid, best_ask):
    while hbt.elapse(1 * 1e9) == 0:
        # Records data points
        local_timestamp.append(hbt.current_timestamp)

        depth = hbt.depth(0)

        best_bid.append(depth.best_bid)
        best_ask.append(depth.best_ask)
    return True

local_timestamp = List.empty_list(int64, allocated=10000)
best_bid = List.empty_list(float64, allocated=10000)
best_ask = List.empty_list(float64, allocated=10000)

hbt = HashMapMarketDepthBacktest([asset])

plot_bbo(hbt, local_timestamp, best_bid, best_ask)

hbt.close()

df = pl.DataFrame({'timestamp': local_timestamp, 'best_bid': best_bid, 'best_ask': best_ask})
df = df.with_columns(
    pl.from_epoch('timestamp', time_unit='ns')
)


import hvplot.polars
df.hvplot(x='timestamp')



:NdOverlay   [Variable]
   :Curve   [timestamp]   (value)

In [ ]:
@njit
def submit_order_stats(hbt, recorder):
    buy_order_id = 1
    sell_order_id = 2
    half_spread = 10 * hbt.depth(0).tick_size

    while hbt.elapse(1 * 1e9) == 0:
        hbt.clear_inactive_orders(0)

        depth = hbt.depth(0)

        mid_price = (depth.best_bid + depth.best_ask) / 2.0

        if buy_order_id not in hbt.orders(0):
            order_price = round((mid_price - half_spread) / depth.tick_size) * depth.tick_size
            order_qty = 1
            time_in_force = GTX
            order_type = LIMIT
            hbt.submit_buy_order(0, buy_order_id, order_price, order_qty, time_in_force, order_type, False)
        else:
            hbt.cancel(0, buy_order_id, False)

        if sell_order_id not in hbt.orders(0):
            order_price = round((mid_price + half_spread) / depth.tick_size) * depth.tick_size
            order_qty = 1
            time_in_force = GTX
            order_type = LIMIT
            hbt.submit_sell_order(0, sell_order_id, order_price, order_qty, time_in_force, order_type, False)
        else:
            hbt.cancel(0, sell_order_id, False)

        recorder.record(hbt)
    return True

hbt = HashMapMarketDepthBacktest([asset])

recorder = Recorder(
    # The number of assets
    hbt.num_assets,
    # The buffer size for records
    1000000
)

submit_order_stats(hbt, recorder.recorder)

_ = hbt.close()

recorder.get(0)


In [ ]:
recorder.get(0)